# CatBoostモデルを用いるシート

In [4]:
from catboost import CatBoostRegressor
from catboost import Pool

In [5]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
import ipywidgets

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]], over100m2, bt75and100m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]], test_over100m2, test_bt75and100m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S', '100m^2以上', '75m^2以上100m^2未満']

In [3]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        early_stopping_rounds=10,
        learning_rate=0.05, 
        depth=6, 
        loss_function='RMSE', 
        l2_leaf_reg=0.0001
        )

    model.fit(X_tr, y_tr, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71188.9241664	total: 59.2ms	remaining: 59.1s
1:	learn: 68688.4187199	total: 61.5ms	remaining: 30.7s
2:	learn: 66345.6485263	total: 64.1ms	remaining: 21.3s
3:	learn: 64115.5745278	total: 66.4ms	remaining: 16.5s
4:	learn: 62093.7735571	total: 68.4ms	remaining: 13.6s
5:	learn: 60081.0336810	total: 70.6ms	remaining: 11.7s
6:	learn: 58109.6452864	total: 72.6ms	remaining: 10.3s
7:	learn: 56308.0493380	total: 74.5ms	remaining: 9.23s
8:	learn: 54524.4356038	total: 76.7ms	remaining: 8.45s
9:	learn: 52900.2010815	total: 78.9ms	remaining: 7.81s
10:	learn: 51353.2812247	total: 80.8ms	remaining: 7.26s
11:	learn: 49941.4171476	total: 82.7ms	remaining: 6.81s
12:	learn: 48559.7159805	total: 84.8ms	remaining: 6.44s
13:	learn: 47231.5663788	total: 87.3ms	remaining: 6.15s
14:	learn: 45984.1431313	total: 89.5ms	remaining: 5.88s
15:	learn: 44776.6530239	total: 91.5ms	remaining: 5.63s
16:	learn: 43671.3080824	total: 93.7ms	remaining: 5.42s
17:	learn: 42625.7315867	total: 95.7ms	remaining: 5.22s
18

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70770.7043393	total: 1.93ms	remaining: 1.93s
1:	learn: 68357.7231050	total: 3.77ms	remaining: 1.88s
2:	learn: 66042.8975168	total: 5.37ms	remaining: 1.78s
3:	learn: 63930.6855774	total: 7.26ms	remaining: 1.81s
4:	learn: 61807.2656063	total: 9.38ms	remaining: 1.87s
5:	learn: 59775.4575601	total: 12.2ms	remaining: 2.02s
6:	learn: 57965.5608590	total: 15.1ms	remaining: 2.15s
7:	learn: 56198.4201710	total: 17.8ms	remaining: 2.2s
8:	learn: 54439.8864053	total: 19.8ms	remaining: 2.18s
9:	learn: 52863.9228997	total: 22.2ms	remaining: 2.2s
10:	learn: 51373.3999800	total: 24.4ms	remaining: 2.19s
11:	learn: 49959.0916205	total: 26.5ms	remaining: 2.19s
12:	learn: 48564.0819849	total: 28.8ms	remaining: 2.19s
13:	learn: 47282.5268125	total: 31.6ms	remaining: 2.22s
14:	learn: 46118.2392061	total: 33.9ms	remaining: 2.23s
15:	learn: 44918.0322357	total: 35.9ms	remaining: 2.21s
16:	learn: 43824.3167057	total: 38.3ms	remaining: 2.21s
17:	learn: 42718.6100340	total: 40.5ms	remaining: 2.21s
18:	

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70787.1802142	total: 2.14ms	remaining: 2.14s
1:	learn: 68331.6600116	total: 3.99ms	remaining: 1.99s
2:	learn: 66066.9384735	total: 5.77ms	remaining: 1.92s
3:	learn: 63892.6359448	total: 7.37ms	remaining: 1.84s
4:	learn: 61742.1115317	total: 9.28ms	remaining: 1.85s
5:	learn: 59771.6486909	total: 11.7ms	remaining: 1.94s
6:	learn: 57928.9466475	total: 14.2ms	remaining: 2.02s
7:	learn: 56142.9819914	total: 17.2ms	remaining: 2.13s
8:	learn: 54430.4989921	total: 19.7ms	remaining: 2.17s
9:	learn: 52845.8554541	total: 22ms	remaining: 2.17s
10:	learn: 51309.0142123	total: 24.3ms	remaining: 2.19s
11:	learn: 49823.8137938	total: 26.5ms	remaining: 2.19s
12:	learn: 48420.1263093	total: 29ms	remaining: 2.2s
13:	learn: 47068.3852480	total: 31.7ms	remaining: 2.23s
14:	learn: 45876.0322324	total: 34.3ms	remaining: 2.25s
15:	learn: 44673.4219682	total: 36.6ms	remaining: 2.25s
16:	learn: 43545.5101006	total: 38.9ms	remaining: 2.25s
17:	learn: 42543.6126550	total: 41.3ms	remaining: 2.25s
18:	lea

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71460.3109651	total: 2.51ms	remaining: 2.51s
1:	learn: 68991.0387080	total: 4.46ms	remaining: 2.22s
2:	learn: 66647.1154003	total: 6.32ms	remaining: 2.1s
3:	learn: 64350.9110736	total: 8.15ms	remaining: 2.03s
4:	learn: 62192.0977510	total: 10.6ms	remaining: 2.1s
5:	learn: 60224.8079770	total: 13.1ms	remaining: 2.16s
6:	learn: 58298.8775427	total: 15.9ms	remaining: 2.26s
7:	learn: 56532.6279870	total: 18.3ms	remaining: 2.27s
8:	learn: 54686.0372942	total: 20.5ms	remaining: 2.25s
9:	learn: 53066.2711868	total: 22.8ms	remaining: 2.25s
10:	learn: 51456.3514504	total: 25.2ms	remaining: 2.26s
11:	learn: 49897.5543185	total: 27.9ms	remaining: 2.3s
12:	learn: 48453.5337521	total: 29.9ms	remaining: 2.27s
13:	learn: 47180.0696440	total: 32ms	remaining: 2.25s
14:	learn: 45925.6945196	total: 34.2ms	remaining: 2.25s
15:	learn: 44697.8646752	total: 36.5ms	remaining: 2.24s
16:	learn: 43571.6430576	total: 39.2ms	remaining: 2.26s
17:	learn: 42430.6126910	total: 41.6ms	remaining: 2.27s
18:	lea

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70335.6320291	total: 2.9ms	remaining: 2.9s
1:	learn: 67981.8966061	total: 4.91ms	remaining: 2.45s
2:	learn: 65705.2226003	total: 6.63ms	remaining: 2.2s
3:	learn: 63580.3822739	total: 8.56ms	remaining: 2.13s
4:	learn: 61512.5220057	total: 11.8ms	remaining: 2.34s
5:	learn: 59601.2419926	total: 14.9ms	remaining: 2.46s
6:	learn: 57755.4244412	total: 17.2ms	remaining: 2.44s
7:	learn: 56048.4588818	total: 20ms	remaining: 2.48s
8:	learn: 54320.7053468	total: 22.2ms	remaining: 2.44s
9:	learn: 52742.2300640	total: 24.6ms	remaining: 2.43s
10:	learn: 51240.8437095	total: 27ms	remaining: 2.42s
11:	learn: 49833.1736889	total: 28.8ms	remaining: 2.37s
12:	learn: 48437.7689955	total: 30.9ms	remaining: 2.35s
13:	learn: 47104.1660034	total: 33.1ms	remaining: 2.33s
14:	learn: 45979.1055703	total: 35.9ms	remaining: 2.35s
15:	learn: 44749.9653623	total: 38ms	remaining: 2.34s
16:	learn: 43645.8487158	total: 40.3ms	remaining: 2.33s
17:	learn: 42608.0031776	total: 42.5ms	remaining: 2.32s
18:	learn: 

catboostのチューニングを行う

In [78]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)
    

        params = {
            'loss_function':'RMSE',
            'learning_rate':0.05,
            'iterations':5000,
            # 'calc_feature_importance': True,
            'use_best_model':True,
            # 'eval_metric':'rmse',
            'depth':trial.suggest_int('depth', 4, 10),
            'l2_leaf_reg':trial.suggest_float('l2_leaf_reg', 0.0000001, 0.0001, log=True),
            'random_strength' :trial.suggest_int('random_strength', 0, 100),
            'bagging_temperature' :trial.suggest_loguniform('bagging_temperature', 0.01, 100.00),
            'od_type': trial.suggest_categorical('od_type', ['IncToDec', 'Iter']),
            'od_wait' :trial.suggest_int('od_wait', 10, 50)    
        }

        model = CatBoostRegressor(**params)
        model.fit(X_tr, y_tr, 
            cat_features=category_lists,
            eval_set=[(X_val, y_val)],
            early_stopping_rounds=100,
            plot=True
        )
        y_pred_val = model.predict(X_val)
        
        rmse_score = mean_squared_error(y_val, y_pred_val, squared=False)
    loss = np.mean(rmse_score)
    return loss

In [79]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-15 19:02:26,221] A new study created in memory with name: no-name-321bfab4-da32-41e7-940b-e6c4b8ff1c84
/var/folders/qh/20ftf7rn5_58_rk3l25kt1nr0000gn/T/ipykernel_5468/4073598087.py:28: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'bagging_temperature' :trial.suggest_loguniform('bagging_temperature', 0.01, 100.00),


MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72762.7292810	test: 71490.9380778	best: 71490.9380778 (0)	total: 16.5ms	remaining: 1m 22s
1:	learn: 72124.8966704	test: 70901.6431514	best: 70901.6431514 (1)	total: 20.8ms	remaining: 51.9s
2:	learn: 71203.3322849	test: 69998.5100608	best: 69998.5100608 (2)	total: 31.1ms	remaining: 51.9s
3:	learn: 69389.4034257	test: 68395.4291333	best: 68395.4291333 (3)	total: 41.5ms	remaining: 51.8s
4:	learn: 67677.5815001	test: 66794.3370948	best: 66794.3370948 (4)	total: 48.4ms	remaining: 48.4s
5:	learn: 66478.9092343	test: 65675.7808461	best: 65675.7808461 (5)	total: 55.9ms	remaining: 46.5s
6:	learn: 65768.6652492	test: 65009.4570858	best: 65009.4570858 (6)	total: 66.6ms	remaining: 47.5s
7:	learn: 64271.7175414	test: 63672.1296879	best: 63672.1296879 (7)	total: 77.1ms	remaining: 48.1s
8:	learn: 62992.9283015	test: 62446.1536348	best: 62446.1536348 (8)	total: 83.4ms	remaining: 46.3s
9:	learn: 62312.3821251	test: 61788.5394338	best: 61788.5394338 (9)	total: 88.5ms	remaining: 44.2s
10:	learn

[W 2022-09-15 19:03:02,721] Trial 0 failed because of the following error: CatBoostError('y may be None only when X is an instance of catboost.Pool or string')
Traceback (most recent call last):
  File "/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/optuna/study/_optimize.py", line 196, in _run_trial
    value_or_values = func(trial)
  File "/var/folders/qh/20ftf7rn5_58_rk3l25kt1nr0000gn/T/ipykernel_5468/4073598087.py", line 40, in objective
    y_pred_val = model.fit(X_val)
  File "/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/catboost/core.py", line 5590, in fit
    return self._fit(X, y, cat_features, None, None, None, sample_weight, None, None, None, None, baseline,
  File "/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/catboost/core.py", line 2260, in _fit
    raise CatBoostError("y may be None only when X is an instance of catboost.Pool or string")
_catboost.CatBoostError: y may be None onl

CatBoostError: y may be None only when X is an instance of catboost.Pool or string

In [ ]:
study.best_params

チューニングしたパラメータを使ってみる

In [8]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        early_stopping_rounds=10,
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    model.fit(X_tr, y_tr, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71839.0626718	total: 5.01ms	remaining: 5.01s
1:	learn: 70369.7580399	total: 8.23ms	remaining: 4.11s
2:	learn: 68810.5448575	total: 11.4ms	remaining: 3.78s
3:	learn: 67878.0760712	total: 12.8ms	remaining: 3.19s
4:	learn: 66071.3770359	total: 16.8ms	remaining: 3.35s
5:	learn: 64528.3221813	total: 19.9ms	remaining: 3.29s
6:	learn: 62930.4497909	total: 22.6ms	remaining: 3.21s
7:	learn: 61593.9294503	total: 25.1ms	remaining: 3.12s
8:	learn: 60382.0640023	total: 27.8ms	remaining: 3.06s
9:	learn: 59176.7243685	total: 30.8ms	remaining: 3.04s
10:	learn: 57933.8081327	total: 33.7ms	remaining: 3.03s
11:	learn: 56995.2148835	total: 36.6ms	remaining: 3.01s
12:	learn: 55936.8829849	total: 39ms	remaining: 2.96s
13:	learn: 54877.3778557	total: 41.4ms	remaining: 2.91s
14:	learn: 53442.4855246	total: 44.1ms	remaining: 2.9s
15:	learn: 52577.4886358	total: 47.6ms	remaining: 2.92s
16:	learn: 51717.6267632	total: 50.4ms	remaining: 2.91s
17:	learn: 50978.0912924	total: 52.7ms	remaining: 2.88s
18:	l

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71476.5949275	total: 3.06ms	remaining: 3.06s
1:	learn: 69892.7115005	total: 6.05ms	remaining: 3.02s
2:	learn: 68585.2173967	total: 9.71ms	remaining: 3.23s
3:	learn: 67670.9711953	total: 11ms	remaining: 2.73s
4:	learn: 65876.4484244	total: 14.6ms	remaining: 2.91s
5:	learn: 64214.9298554	total: 17.3ms	remaining: 2.87s
6:	learn: 62649.2631673	total: 19.9ms	remaining: 2.83s
7:	learn: 61296.7189346	total: 22.5ms	remaining: 2.79s
8:	learn: 60157.6410467	total: 25.8ms	remaining: 2.85s
9:	learn: 58928.7956129	total: 29.4ms	remaining: 2.91s
10:	learn: 57694.9936784	total: 31.9ms	remaining: 2.87s
11:	learn: 56830.9419646	total: 34.5ms	remaining: 2.84s
12:	learn: 55789.4216785	total: 37.3ms	remaining: 2.83s
13:	learn: 54795.1369426	total: 39.9ms	remaining: 2.81s
14:	learn: 53432.2399242	total: 43.3ms	remaining: 2.84s
15:	learn: 52600.5057463	total: 46.7ms	remaining: 2.87s
16:	learn: 51791.6940355	total: 49.5ms	remaining: 2.86s
17:	learn: 51061.1797907	total: 51.8ms	remaining: 2.83s
18:	

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71485.8345005	total: 3.05ms	remaining: 3.05s
1:	learn: 70068.6309166	total: 5.29ms	remaining: 2.64s
2:	learn: 68772.1273398	total: 7.45ms	remaining: 2.48s
3:	learn: 67864.5976469	total: 8.73ms	remaining: 2.17s
4:	learn: 66136.3011355	total: 11.9ms	remaining: 2.36s
5:	learn: 64486.1959177	total: 15ms	remaining: 2.48s
6:	learn: 62945.7933270	total: 18.1ms	remaining: 2.56s
7:	learn: 61561.2772442	total: 21.3ms	remaining: 2.64s
8:	learn: 60427.4857810	total: 23.9ms	remaining: 2.63s
9:	learn: 59229.8675091	total: 27.4ms	remaining: 2.72s
10:	learn: 58022.5995661	total: 30.6ms	remaining: 2.75s
11:	learn: 57276.8446141	total: 33.6ms	remaining: 2.77s
12:	learn: 56252.5719399	total: 36.3ms	remaining: 2.76s
13:	learn: 55265.0554017	total: 39.3ms	remaining: 2.76s
14:	learn: 53875.8135603	total: 42ms	remaining: 2.76s
15:	learn: 53048.5859767	total: 45.2ms	remaining: 2.78s
16:	learn: 52235.3598739	total: 47.7ms	remaining: 2.76s
17:	learn: 51521.1112026	total: 50.6ms	remaining: 2.76s
18:	le

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72168.2713572	total: 2.79ms	remaining: 2.79s
1:	learn: 70553.2618976	total: 6.4ms	remaining: 3.19s
2:	learn: 69262.4032386	total: 9.23ms	remaining: 3.07s
3:	learn: 68335.0239225	total: 10.4ms	remaining: 2.58s
4:	learn: 66568.0438783	total: 13.2ms	remaining: 2.62s
5:	learn: 65026.2647701	total: 15.7ms	remaining: 2.6s
6:	learn: 63428.1017117	total: 18.6ms	remaining: 2.64s
7:	learn: 62050.6174236	total: 21.2ms	remaining: 2.63s
8:	learn: 60839.8842561	total: 24.2ms	remaining: 2.67s
9:	learn: 59635.2618822	total: 27.2ms	remaining: 2.69s
10:	learn: 58374.7438088	total: 29.7ms	remaining: 2.67s
11:	learn: 57603.9991994	total: 32ms	remaining: 2.64s
12:	learn: 56555.3421010	total: 34.6ms	remaining: 2.62s
13:	learn: 55539.8290519	total: 37.2ms	remaining: 2.62s
14:	learn: 54148.7751711	total: 40.1ms	remaining: 2.63s
15:	learn: 53288.3937464	total: 42.6ms	remaining: 2.62s
16:	learn: 52439.1756449	total: 45.2ms	remaining: 2.61s
17:	learn: 51718.9353548	total: 47.6ms	remaining: 2.6s
18:	lea

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70957.3168050	total: 2.58ms	remaining: 2.57s
1:	learn: 69371.1816852	total: 4.82ms	remaining: 2.41s
2:	learn: 68060.4377810	total: 6.81ms	remaining: 2.26s
3:	learn: 67144.1815508	total: 7.83ms	remaining: 1.95s
4:	learn: 65408.3168070	total: 10.5ms	remaining: 2.08s
5:	learn: 63769.5905010	total: 13.6ms	remaining: 2.25s
6:	learn: 62220.9127576	total: 17.1ms	remaining: 2.42s
7:	learn: 60902.1544642	total: 20.4ms	remaining: 2.53s
8:	learn: 59744.9350259	total: 23.7ms	remaining: 2.61s
9:	learn: 58591.3884146	total: 26.6ms	remaining: 2.64s
10:	learn: 57386.5339715	total: 29.5ms	remaining: 2.65s
11:	learn: 56637.9531534	total: 32.3ms	remaining: 2.66s
12:	learn: 55597.9444768	total: 35.7ms	remaining: 2.71s
13:	learn: 54582.6581436	total: 38.8ms	remaining: 2.73s
14:	learn: 53196.4987492	total: 41.7ms	remaining: 2.73s
15:	learn: 51942.1141068	total: 44.2ms	remaining: 2.72s
16:	learn: 50971.9448482	total: 47.2ms	remaining: 2.73s
17:	learn: 50266.6324069	total: 51.1ms	remaining: 2.79s
18

In [9]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/CatBoost_cv_result.csv',index=False)

特徴量を全て使ってみる

In [10]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, washlets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']], test_sepa_bath_toilets, test_washlets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満']

In [11]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 200, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    model.fit(X_tr, y_tr, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71884.0041334	total: 4.11ms	remaining: 4.11s
1:	learn: 70171.8221412	total: 7.97ms	remaining: 3.98s
2:	learn: 68292.9393594	total: 11.6ms	remaining: 3.84s
3:	learn: 66412.4056256	total: 14.9ms	remaining: 3.7s
4:	learn: 64997.5025741	total: 18.7ms	remaining: 3.73s
5:	learn: 63628.9087313	total: 22.3ms	remaining: 3.69s
6:	learn: 62145.2512428	total: 26ms	remaining: 3.69s
7:	learn: 60804.8496166	total: 30.2ms	remaining: 3.75s
8:	learn: 59980.5788640	total: 31.9ms	remaining: 3.52s
9:	learn: 58507.0029975	total: 35.8ms	remaining: 3.55s
10:	learn: 57236.5226344	total: 39.4ms	remaining: 3.54s
11:	learn: 56409.3590825	total: 41.3ms	remaining: 3.4s
12:	learn: 55329.2767308	total: 45.3ms	remaining: 3.44s
13:	learn: 54255.3108472	total: 48.9ms	remaining: 3.45s
14:	learn: 53442.6701546	total: 53ms	remaining: 3.48s
15:	learn: 52275.9532579	total: 56.3ms	remaining: 3.46s
16:	learn: 51299.1800193	total: 59.8ms	remaining: 3.46s
17:	learn: 50106.7442118	total: 63.4ms	remaining: 3.46s
18:	lear

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71507.2701019	total: 3.62ms	remaining: 3.62s
1:	learn: 69813.8260349	total: 7.11ms	remaining: 3.55s
2:	learn: 67990.2737928	total: 11.5ms	remaining: 3.83s
3:	learn: 66226.2022177	total: 15.6ms	remaining: 3.88s
4:	learn: 64850.6310406	total: 19.9ms	remaining: 3.97s
5:	learn: 63532.4443209	total: 24.1ms	remaining: 3.99s
6:	learn: 62063.5016488	total: 27.5ms	remaining: 3.91s
7:	learn: 60728.4772266	total: 31.4ms	remaining: 3.89s
8:	learn: 59929.1072741	total: 33.2ms	remaining: 3.65s
9:	learn: 58476.5624757	total: 36.8ms	remaining: 3.64s
10:	learn: 57245.7887737	total: 40.5ms	remaining: 3.64s
11:	learn: 56477.3478296	total: 42.8ms	remaining: 3.52s
12:	learn: 55420.9239412	total: 46ms	remaining: 3.5s
13:	learn: 54389.6058481	total: 50ms	remaining: 3.52s
14:	learn: 53606.2534863	total: 53.7ms	remaining: 3.53s
15:	learn: 52467.6477105	total: 57.5ms	remaining: 3.54s
16:	learn: 51552.1446137	total: 61.2ms	remaining: 3.54s
17:	learn: 50374.4505352	total: 64.6ms	remaining: 3.52s
18:	lea

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71533.5809672	total: 3.03ms	remaining: 3.03s
1:	learn: 69855.4534403	total: 6.45ms	remaining: 3.22s
2:	learn: 68039.8394461	total: 10.1ms	remaining: 3.35s
3:	learn: 66266.6742636	total: 13.6ms	remaining: 3.38s
4:	learn: 65226.9911585	total: 18.3ms	remaining: 3.63s
5:	learn: 63902.2791901	total: 22ms	remaining: 3.65s
6:	learn: 62453.1856332	total: 26.3ms	remaining: 3.74s
7:	learn: 61162.1901567	total: 30.3ms	remaining: 3.75s
8:	learn: 59949.7884106	total: 32.1ms	remaining: 3.53s
9:	learn: 58507.2716794	total: 35.8ms	remaining: 3.54s
10:	learn: 57316.9595148	total: 40.1ms	remaining: 3.6s
11:	learn: 56527.5733521	total: 42.9ms	remaining: 3.53s
12:	learn: 55474.3670097	total: 46.5ms	remaining: 3.53s
13:	learn: 54294.9241920	total: 50.7ms	remaining: 3.57s
14:	learn: 53535.0780707	total: 55ms	remaining: 3.61s
15:	learn: 52389.4073026	total: 61.7ms	remaining: 3.8s
16:	learn: 51509.6354831	total: 65.3ms	remaining: 3.78s
17:	learn: 50336.7896421	total: 69.3ms	remaining: 3.78s
18:	lear

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72199.7189044	total: 4ms	remaining: 4s
1:	learn: 70473.2438353	total: 7.68ms	remaining: 3.83s
2:	learn: 68624.0673689	total: 11ms	remaining: 3.64s
3:	learn: 66827.9893717	total: 14.4ms	remaining: 3.59s
4:	learn: 65451.1284271	total: 19ms	remaining: 3.77s
5:	learn: 64108.7958465	total: 22.8ms	remaining: 3.77s
6:	learn: 62609.8351782	total: 26.5ms	remaining: 3.75s
7:	learn: 61273.7789243	total: 30.7ms	remaining: 3.8s
8:	learn: 60470.5156774	total: 32.6ms	remaining: 3.59s
9:	learn: 58990.9117782	total: 36.3ms	remaining: 3.59s
10:	learn: 57791.4946646	total: 40.3ms	remaining: 3.62s
11:	learn: 56997.7255889	total: 42.6ms	remaining: 3.51s
12:	learn: 55918.6927801	total: 46.4ms	remaining: 3.52s
13:	learn: 54886.7636052	total: 50.8ms	remaining: 3.58s
14:	learn: 54133.9772570	total: 54.6ms	remaining: 3.59s
15:	learn: 52753.7137775	total: 58.8ms	remaining: 3.62s
16:	learn: 51780.8418268	total: 62.3ms	remaining: 3.6s
17:	learn: 50628.2765519	total: 66.3ms	remaining: 3.62s
18:	learn: 499

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70972.3374245	total: 4.29ms	remaining: 4.29s
1:	learn: 69273.7100673	total: 7.76ms	remaining: 3.87s
2:	learn: 67432.2328569	total: 11.9ms	remaining: 3.96s
3:	learn: 65652.2137667	total: 15.9ms	remaining: 3.95s
4:	learn: 64635.5997068	total: 20.6ms	remaining: 4.1s
5:	learn: 63281.0660418	total: 24.3ms	remaining: 4.02s
6:	learn: 61827.5261505	total: 28.2ms	remaining: 4s
7:	learn: 60507.1027036	total: 32.1ms	remaining: 3.98s
8:	learn: 59693.7644064	total: 33.8ms	remaining: 3.73s
9:	learn: 58250.7469780	total: 37.6ms	remaining: 3.73s
10:	learn: 56994.8237053	total: 41.5ms	remaining: 3.73s
11:	learn: 56197.4121413	total: 43.7ms	remaining: 3.6s
12:	learn: 55129.2050736	total: 47.6ms	remaining: 3.62s
13:	learn: 54091.0749291	total: 51.5ms	remaining: 3.63s
14:	learn: 53291.3569585	total: 55.7ms	remaining: 3.66s
15:	learn: 52163.1318219	total: 59.2ms	remaining: 3.64s
16:	learn: 51213.4762309	total: 63.2ms	remaining: 3.66s
17:	learn: 50072.5877799	total: 66.8ms	remaining: 3.65s
18:	lea

In [12]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/CatBoost_cv_result.csv',index=False)

### CatBoostにおいて「温水洗浄便座」と「方角」を除いた場合

In [13]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [14]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 200, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72725.6816902	test: 71381.2629992	best: 71381.2629992 (0)	total: 11.8ms	remaining: 2.35s
1:	learn: 70736.1722160	test: 69444.4824417	best: 69444.4824417 (1)	total: 29.3ms	remaining: 2.9s
2:	learn: 68975.0476279	test: 67801.7375254	best: 67801.7375254 (2)	total: 41.2ms	remaining: 2.7s
3:	learn: 67471.6559784	test: 66360.3015347	best: 66360.3015347 (3)	total: 50.3ms	remaining: 2.47s
4:	learn: 66167.2240064	test: 65151.6223117	best: 65151.6223117 (4)	total: 62.6ms	remaining: 2.44s
5:	learn: 64173.5642750	test: 63436.0023526	best: 63436.0023526 (5)	total: 74ms	remaining: 2.39s
6:	learn: 63131.9067326	test: 62436.6760154	best: 62436.6760154 (6)	total: 80.7ms	remaining: 2.22s
7:	learn: 61334.1999591	test: 60950.3600702	best: 60950.3600702 (7)	total: 86.8ms	remaining: 2.08s
8:	learn: 60136.8297337	test: 59803.6769043	best: 59803.6769043 (8)	total: 93.3ms	remaining: 1.98s
9:	learn: 59055.6139758	test: 58765.3996240	best: 58765.3996240 (9)	total: 104ms	remaining: 1.98s
10:	learn: 5887

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72360.5459165	test: 72880.1979329	best: 72880.1979329 (0)	total: 3.03ms	remaining: 602ms
1:	learn: 70388.3773817	test: 70910.2077920	best: 70910.2077920 (1)	total: 12.1ms	remaining: 1.2s
2:	learn: 68668.1569427	test: 69103.4764707	best: 69103.4764707 (2)	total: 20.4ms	remaining: 1.34s
3:	learn: 67202.7231668	test: 67583.3031731	best: 67583.3031731 (3)	total: 27.1ms	remaining: 1.33s
4:	learn: 65855.1073376	test: 66320.4146547	best: 66320.4146547 (4)	total: 35.7ms	remaining: 1.39s
5:	learn: 63909.5498892	test: 64243.8220883	best: 64243.8220883 (5)	total: 43.2ms	remaining: 1.4s
6:	learn: 62916.0298407	test: 63210.8960757	best: 63210.8960757 (6)	total: 49.4ms	remaining: 1.36s
7:	learn: 61698.8728605	test: 61975.7371533	best: 61975.7371533 (7)	total: 56.2ms	remaining: 1.35s
8:	learn: 60546.4664313	test: 60835.1042355	best: 60835.1042355 (8)	total: 62.9ms	remaining: 1.33s
9:	learn: 59505.1833760	test: 59786.7539936	best: 59786.7539936 (9)	total: 73ms	remaining: 1.39s
10:	learn: 580

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72352.6352553	test: 72946.5643571	best: 72946.5643571 (0)	total: 2.67ms	remaining: 531ms
1:	learn: 70416.8327034	test: 70896.0086886	best: 70896.0086886 (1)	total: 12.9ms	remaining: 1.27s
2:	learn: 68905.2204712	test: 69146.5237511	best: 69146.5237511 (2)	total: 21.3ms	remaining: 1.4s
3:	learn: 67427.6547750	test: 67546.1283430	best: 67546.1283430 (3)	total: 28.2ms	remaining: 1.38s
4:	learn: 66133.0223028	test: 66146.4630078	best: 66146.4630078 (4)	total: 36ms	remaining: 1.4s
5:	learn: 64223.5623970	test: 64207.3724282	best: 64207.3724282 (5)	total: 44.9ms	remaining: 1.45s
6:	learn: 63223.8543885	test: 63131.0155904	best: 63131.0155904 (6)	total: 50.9ms	remaining: 1.4s
7:	learn: 62026.3632517	test: 61853.9047931	best: 61853.9047931 (7)	total: 59.3ms	remaining: 1.42s
8:	learn: 60873.7226360	test: 60609.1160545	best: 60609.1160545 (8)	total: 65.5ms	remaining: 1.39s
9:	learn: 59724.2876621	test: 59399.7723324	best: 59399.7723324 (9)	total: 75.4ms	remaining: 1.43s
10:	learn: 5851

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 73051.7306245	test: 70023.0638894	best: 70023.0638894 (0)	total: 2.8ms	remaining: 557ms
1:	learn: 71065.4641188	test: 68154.5173901	best: 68154.5173901 (1)	total: 12.6ms	remaining: 1.25s
2:	learn: 69321.6552755	test: 66365.3510713	best: 66365.3510713 (2)	total: 22ms	remaining: 1.45s
3:	learn: 67800.9601674	test: 64860.3547807	best: 64860.3547807 (3)	total: 28.3ms	remaining: 1.39s
4:	learn: 65752.9475722	test: 62951.8413254	best: 62951.8413254 (4)	total: 38.8ms	remaining: 1.51s
5:	learn: 64249.3135389	test: 61506.7839334	best: 61506.7839334 (5)	total: 45.3ms	remaining: 1.46s
6:	learn: 62571.1427690	test: 59852.9135081	best: 59852.9135081 (6)	total: 53.1ms	remaining: 1.47s
7:	learn: 61225.3121601	test: 58502.0961451	best: 58502.0961451 (7)	total: 61.6ms	remaining: 1.48s
8:	learn: 59955.4379366	test: 57247.3252605	best: 57247.3252605 (8)	total: 70.4ms	remaining: 1.49s
9:	learn: 59390.0284578	test: 56649.4871349	best: 56649.4871349 (9)	total: 74.5ms	remaining: 1.42s
10:	learn: 58

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71818.5392550	test: 75007.9087839	best: 75007.9087839 (0)	total: 3.55ms	remaining: 707ms
1:	learn: 69853.2077288	test: 73038.3280484	best: 73038.3280484 (1)	total: 14.2ms	remaining: 1.4s
2:	learn: 68122.8250164	test: 71291.4134544	best: 71291.4134544 (2)	total: 24.2ms	remaining: 1.59s
3:	learn: 66656.7291762	test: 69746.4637330	best: 69746.4637330 (3)	total: 32.1ms	remaining: 1.57s
4:	learn: 65414.9301161	test: 68312.8018505	best: 68312.8018505 (4)	total: 41.2ms	remaining: 1.6s
5:	learn: 63533.6156125	test: 66345.9783425	best: 66345.9783425 (5)	total: 50.1ms	remaining: 1.62s
6:	learn: 62556.2630129	test: 65306.0658530	best: 65306.0658530 (6)	total: 57.6ms	remaining: 1.59s
7:	learn: 61332.8191693	test: 64039.7635263	best: 64039.7635263 (7)	total: 65.4ms	remaining: 1.57s
8:	learn: 60179.8287708	test: 62849.9848096	best: 62849.9848096 (8)	total: 72.2ms	remaining: 1.53s
9:	learn: 58628.7224213	test: 61365.2874088	best: 61365.2874088 (9)	total: 81.3ms	remaining: 1.54s
10:	learn: 5

## 色々パラメータをいじってみる！

In [20]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

繰り返し回数を増やす

In [21]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72725.6816902	test: 71381.2629992	best: 71381.2629992 (0)	total: 2.55ms	remaining: 5.1s
1:	learn: 70736.1722160	test: 69444.4824417	best: 69444.4824417 (1)	total: 11.6ms	remaining: 11.5s
2:	learn: 68975.0476279	test: 67801.7375254	best: 67801.7375254 (2)	total: 20.8ms	remaining: 13.9s
3:	learn: 67471.6559784	test: 66360.3015347	best: 66360.3015347 (3)	total: 29.7ms	remaining: 14.8s
4:	learn: 66167.2240064	test: 65151.6223117	best: 65151.6223117 (4)	total: 38.7ms	remaining: 15.4s
5:	learn: 64173.5642750	test: 63436.0023526	best: 63436.0023526 (5)	total: 47.7ms	remaining: 15.8s
6:	learn: 63131.9067326	test: 62436.6760154	best: 62436.6760154 (6)	total: 55.4ms	remaining: 15.8s
7:	learn: 61334.1999591	test: 60950.3600702	best: 60950.3600702 (7)	total: 62.2ms	remaining: 15.5s
8:	learn: 60136.8297337	test: 59803.6769043	best: 59803.6769043 (8)	total: 83.1ms	remaining: 18.4s
9:	learn: 59055.6139758	test: 58765.3996240	best: 58765.3996240 (9)	total: 109ms	remaining: 21.6s
10:	learn: 5

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72360.5459165	test: 72880.1979329	best: 72880.1979329 (0)	total: 2.38ms	remaining: 4.76s
1:	learn: 70388.3773817	test: 70910.2077920	best: 70910.2077920 (1)	total: 12.9ms	remaining: 12.9s
2:	learn: 68668.1569427	test: 69103.4764707	best: 69103.4764707 (2)	total: 22.9ms	remaining: 15.3s
3:	learn: 67202.7231668	test: 67583.3031731	best: 67583.3031731 (3)	total: 30.7ms	remaining: 15.3s
4:	learn: 65855.1073376	test: 66320.4146547	best: 66320.4146547 (4)	total: 39ms	remaining: 15.6s
5:	learn: 63909.5498892	test: 64243.8220883	best: 64243.8220883 (5)	total: 48.8ms	remaining: 16.2s
6:	learn: 62916.0298407	test: 63210.8960757	best: 63210.8960757 (6)	total: 56.3ms	remaining: 16s
7:	learn: 61698.8728605	test: 61975.7371533	best: 61975.7371533 (7)	total: 64.7ms	remaining: 16.1s
8:	learn: 60546.4664313	test: 60835.1042355	best: 60835.1042355 (8)	total: 72.2ms	remaining: 16s
9:	learn: 59505.1833760	test: 59786.7539936	best: 59786.7539936 (9)	total: 81.7ms	remaining: 16.3s
10:	learn: 58074

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72352.6352553	test: 72946.5643571	best: 72946.5643571 (0)	total: 2.09ms	remaining: 4.18s
1:	learn: 70416.8327034	test: 70896.0086886	best: 70896.0086886 (1)	total: 12ms	remaining: 11.9s
2:	learn: 68905.2204712	test: 69146.5237511	best: 69146.5237511 (2)	total: 21.6ms	remaining: 14.4s
3:	learn: 67427.6547750	test: 67546.1283430	best: 67546.1283430 (3)	total: 29.1ms	remaining: 14.5s
4:	learn: 66133.0223028	test: 66146.4630078	best: 66146.4630078 (4)	total: 37.8ms	remaining: 15.1s
5:	learn: 64223.5623970	test: 64207.3724282	best: 64207.3724282 (5)	total: 46.2ms	remaining: 15.3s
6:	learn: 63223.8543885	test: 63131.0155904	best: 63131.0155904 (6)	total: 62.3ms	remaining: 17.7s
7:	learn: 62026.3632517	test: 61853.9047931	best: 61853.9047931 (7)	total: 74.8ms	remaining: 18.6s
8:	learn: 60873.7226360	test: 60609.1160545	best: 60609.1160545 (8)	total: 83.3ms	remaining: 18.4s
9:	learn: 59724.2876621	test: 59399.7723324	best: 59399.7723324 (9)	total: 91.5ms	remaining: 18.2s
10:	learn: 5

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 73051.7306245	test: 70023.0638894	best: 70023.0638894 (0)	total: 2.61ms	remaining: 5.21s
1:	learn: 71065.4641188	test: 68154.5173901	best: 68154.5173901 (1)	total: 12.7ms	remaining: 12.6s
2:	learn: 69321.6552755	test: 66365.3510713	best: 66365.3510713 (2)	total: 21.5ms	remaining: 14.3s
3:	learn: 67800.9601674	test: 64860.3547807	best: 64860.3547807 (3)	total: 29.9ms	remaining: 14.9s
4:	learn: 65752.9475722	test: 62951.8413254	best: 62951.8413254 (4)	total: 40.2ms	remaining: 16.1s
5:	learn: 64249.3135389	test: 61506.7839334	best: 61506.7839334 (5)	total: 48.4ms	remaining: 16.1s
6:	learn: 62571.1427690	test: 59852.9135081	best: 59852.9135081 (6)	total: 55.7ms	remaining: 15.9s
7:	learn: 61225.3121601	test: 58502.0961451	best: 58502.0961451 (7)	total: 65.1ms	remaining: 16.2s
8:	learn: 59955.4379366	test: 57247.3252605	best: 57247.3252605 (8)	total: 73.3ms	remaining: 16.2s
9:	learn: 59390.0284578	test: 56649.4871349	best: 56649.4871349 (9)	total: 77.8ms	remaining: 15.5s
10:	learn:

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71818.5392550	test: 75007.9087839	best: 75007.9087839 (0)	total: 2.63ms	remaining: 5.25s
1:	learn: 69853.2077288	test: 73038.3280484	best: 73038.3280484 (1)	total: 11.8ms	remaining: 11.8s
2:	learn: 68122.8250164	test: 71291.4134544	best: 71291.4134544 (2)	total: 20.6ms	remaining: 13.7s
3:	learn: 66656.7291762	test: 69746.4637330	best: 69746.4637330 (3)	total: 28.3ms	remaining: 14.1s
4:	learn: 65414.9301161	test: 68312.8018505	best: 68312.8018505 (4)	total: 37.3ms	remaining: 14.9s
5:	learn: 63533.6156125	test: 66345.9783425	best: 66345.9783425 (5)	total: 45.5ms	remaining: 15.1s
6:	learn: 62556.2630129	test: 65306.0658530	best: 65306.0658530 (6)	total: 52.5ms	remaining: 14.9s
7:	learn: 61332.8191693	test: 64039.7635263	best: 64039.7635263 (7)	total: 59.3ms	remaining: 14.8s
8:	learn: 60179.8287708	test: 62849.9848096	best: 62849.9848096 (8)	total: 65.8ms	remaining: 14.6s
9:	learn: 58628.7224213	test: 61365.2874088	best: 61365.2874088 (9)	total: 75ms	remaining: 14.9s
10:	learn: 5

2000回くらいあれば十分そう

In [22]:
y_pred

array([129137.36227629, 123541.86056723,  75855.99630592, ...,
       174612.41459827, 249113.06800902,  82001.44542646])

### 特徴量を減らす

カテゴリ変数以外で重要性の低いものを除外してみる

まずは部屋数を除外してみる

In [24]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [25]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71570.4687164	test: 70518.0237773	best: 70518.0237773 (0)	total: 8.76ms	remaining: 17.5s
1:	learn: 70811.0168856	test: 69757.1432750	best: 69757.1432750 (1)	total: 11.7ms	remaining: 11.7s
2:	learn: 69395.9316813	test: 68361.8866422	best: 68361.8866422 (2)	total: 14.5ms	remaining: 9.66s
3:	learn: 67755.3069958	test: 66782.0793463	best: 66782.0793463 (3)	total: 22.3ms	remaining: 11.1s
4:	learn: 66248.3650061	test: 65382.4777400	best: 65382.4777400 (4)	total: 29.6ms	remaining: 11.8s
5:	learn: 65051.4278061	test: 64369.4612099	best: 64369.4612099 (5)	total: 36ms	remaining: 12s
6:	learn: 63632.3195914	test: 62917.9359611	best: 62917.9359611 (6)	total: 44.8ms	remaining: 12.7s
7:	learn: 62500.5828609	test: 61830.6161500	best: 61830.6161500 (7)	total: 48.3ms	remaining: 12s
8:	learn: 61028.9036029	test: 60421.6104212	best: 60421.6104212 (8)	total: 56.3ms	remaining: 12.4s
9:	learn: 59508.2423803	test: 58975.7547381	best: 58975.7547381 (9)	total: 62.8ms	remaining: 12.5s
10:	learn: 58333

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71401.6555021	test: 72007.4234290	best: 72007.4234290 (0)	total: 9.68ms	remaining: 19.3s
1:	learn: 70647.9287260	test: 71250.0049893	best: 71250.0049893 (1)	total: 12.3ms	remaining: 12.3s
2:	learn: 69281.5474994	test: 69857.0486869	best: 69857.0486869 (2)	total: 15.5ms	remaining: 10.3s
3:	learn: 67696.9881927	test: 68240.0450735	best: 68240.0450735 (3)	total: 25ms	remaining: 12.5s
4:	learn: 66209.0424147	test: 66689.2907925	best: 66689.2907925 (4)	total: 33.2ms	remaining: 13.2s
5:	learn: 65091.2579128	test: 65497.5508521	best: 65497.5508521 (5)	total: 39.8ms	remaining: 13.2s
6:	learn: 63704.3874686	test: 64008.7214159	best: 64008.7214159 (6)	total: 50.7ms	remaining: 14.4s
7:	learn: 62596.7859779	test: 62896.7447341	best: 62896.7447341 (7)	total: 54.8ms	remaining: 13.6s
8:	learn: 61144.3249446	test: 61379.8613230	best: 61379.8613230 (8)	total: 62ms	remaining: 13.7s
9:	learn: 59674.8508104	test: 59855.7294325	best: 59855.7294325 (9)	total: 68.3ms	remaining: 13.6s
10:	learn: 585

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71494.3015453	test: 72046.4462348	best: 72046.4462348 (0)	total: 9.12ms	remaining: 18.2s
1:	learn: 70752.5826094	test: 71270.1411627	best: 71270.1411627 (1)	total: 12ms	remaining: 12s
2:	learn: 69401.3646213	test: 69798.3186718	best: 69798.3186718 (2)	total: 15.5ms	remaining: 10.3s
3:	learn: 67812.4386353	test: 68074.3806521	best: 68074.3806521 (3)	total: 23.3ms	remaining: 11.6s
4:	learn: 66348.1168983	test: 66523.8858574	best: 66523.8858574 (4)	total: 29.7ms	remaining: 11.8s
5:	learn: 65228.4556844	test: 65310.6434865	best: 65310.6434865 (5)	total: 36.1ms	remaining: 12s
6:	learn: 63868.9368796	test: 63759.6914543	best: 63759.6914543 (6)	total: 44.9ms	remaining: 12.8s
7:	learn: 62771.1505605	test: 62585.1162442	best: 62585.1162442 (7)	total: 49.2ms	remaining: 12.2s
8:	learn: 61382.4411217	test: 61033.7355375	best: 61033.7355375 (8)	total: 55.5ms	remaining: 12.3s
9:	learn: 59931.8331473	test: 59355.3764118	best: 59355.3764118 (9)	total: 62.1ms	remaining: 12.4s
10:	learn: 58806

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72010.5342127	test: 68960.4147350	best: 68960.4147350 (0)	total: 9.56ms	remaining: 19.1s
1:	learn: 71245.2555169	test: 68199.1040263	best: 68199.1040263 (1)	total: 12.4ms	remaining: 12.4s
2:	learn: 69842.5743532	test: 66785.1067418	best: 66785.1067418 (2)	total: 15.9ms	remaining: 10.6s
3:	learn: 68224.1269257	test: 65211.7130076	best: 65211.7130076 (3)	total: 26.7ms	remaining: 13.3s
4:	learn: 66767.0454828	test: 63695.4520332	best: 63695.4520332 (4)	total: 33.8ms	remaining: 13.5s
5:	learn: 65622.7707102	test: 62613.7440521	best: 62613.7440521 (5)	total: 41ms	remaining: 13.6s
6:	learn: 64250.1298799	test: 61184.7971112	best: 61184.7971112 (6)	total: 49.8ms	remaining: 14.2s
7:	learn: 63120.6422425	test: 60100.9514967	best: 60100.9514967 (7)	total: 53.7ms	remaining: 13.4s
8:	learn: 61700.5297765	test: 58670.4581645	best: 58670.4581645 (8)	total: 61ms	remaining: 13.5s
9:	learn: 60198.5870161	test: 57203.3070901	best: 57203.3070901 (9)	total: 67.3ms	remaining: 13.4s
10:	learn: 590

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70921.8356540	test: 74106.5470206	best: 74106.5470206 (0)	total: 7.22ms	remaining: 14.4s
1:	learn: 70157.8728579	test: 73378.0390545	best: 73378.0390545 (1)	total: 10.2ms	remaining: 10.2s
2:	learn: 68786.0798367	test: 71969.7667365	best: 71969.7667365 (2)	total: 12.6ms	remaining: 8.38s
3:	learn: 67176.7133409	test: 70357.4817854	best: 70357.4817854 (3)	total: 21.3ms	remaining: 10.6s
4:	learn: 65739.8308834	test: 68880.6618279	best: 68880.6618279 (4)	total: 27.8ms	remaining: 11.1s
5:	learn: 64644.6451113	test: 67729.7531997	best: 67729.7531997 (5)	total: 34.4ms	remaining: 11.4s
6:	learn: 63282.5255893	test: 66271.1682548	best: 66271.1682548 (6)	total: 42.9ms	remaining: 12.2s
7:	learn: 62171.5669359	test: 65157.3615520	best: 65157.3615520 (7)	total: 47ms	remaining: 11.7s
8:	learn: 60754.9793190	test: 63712.6311422	best: 63712.6311422 (8)	total: 54.5ms	remaining: 12.1s
9:	learn: 59284.6667351	test: 62274.1799129	best: 62274.1799129 (9)	total: 60.1ms	remaining: 12s
10:	learn: 581

「部屋数」を除外したら少し良くなった！

次は「所要時間」も除外してみる

In [26]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, land_aveprice, addresses, room_arrange[["L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_land_aveprice, test_addresses, test_room_arrange[["L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [27]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72011.6086141	test: 70719.4290918	best: 70719.4290918 (0)	total: 9.49ms	remaining: 19s
1:	learn: 70034.7939059	test: 68935.6137335	best: 68935.6137335 (1)	total: 18.8ms	remaining: 18.8s
2:	learn: 68558.0646940	test: 67516.2680880	best: 67516.2680880 (2)	total: 27.6ms	remaining: 18.4s
3:	learn: 67165.1964618	test: 66181.7197863	best: 66181.7197863 (3)	total: 34.6ms	remaining: 17.3s
4:	learn: 65750.9640034	test: 64947.3997323	best: 64947.3997323 (4)	total: 38.8ms	remaining: 15.5s
5:	learn: 64377.0205950	test: 63604.4902189	best: 63604.4902189 (5)	total: 46.5ms	remaining: 15.5s
6:	learn: 63100.1715379	test: 62422.7639165	best: 62422.7639165 (6)	total: 52ms	remaining: 14.8s
7:	learn: 61855.3546739	test: 61226.0798866	best: 61226.0798866 (7)	total: 58.3ms	remaining: 14.5s
8:	learn: 61647.3576953	test: 61025.2351305	best: 61025.2351305 (8)	total: 62.6ms	remaining: 13.8s
9:	learn: 60522.4896188	test: 59945.5062532	best: 59945.5062532 (9)	total: 67.5ms	remaining: 13.4s
10:	learn: 591

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71673.1255808	test: 72073.9870759	best: 72073.9870759 (0)	total: 7.92ms	remaining: 15.8s
1:	learn: 69769.7851988	test: 70144.6112860	best: 70144.6112860 (1)	total: 18.2ms	remaining: 18.2s
2:	learn: 68331.7311193	test: 68741.3384397	best: 68741.3384397 (2)	total: 28.6ms	remaining: 19s
3:	learn: 67008.1012521	test: 67308.0989352	best: 67308.0989352 (3)	total: 36.4ms	remaining: 18.2s
4:	learn: 65647.5686774	test: 65917.8999211	best: 65917.8999211 (4)	total: 41.6ms	remaining: 16.6s
5:	learn: 64319.0179447	test: 64546.2667362	best: 64546.2667362 (5)	total: 49.4ms	remaining: 16.4s
6:	learn: 63081.7681115	test: 63288.8822661	best: 63288.8822661 (6)	total: 54.7ms	remaining: 15.6s
7:	learn: 61840.7924840	test: 62047.0528468	best: 62047.0528468 (7)	total: 60.4ms	remaining: 15s
8:	learn: 61377.1328240	test: 61583.9649579	best: 61583.9649579 (8)	total: 65.9ms	remaining: 14.6s
9:	learn: 60961.7490025	test: 61105.8898216	best: 61105.8898216 (9)	total: 68.1ms	remaining: 13.5s
10:	learn: 595

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71666.3224540	test: 72206.8689208	best: 72206.8689208 (0)	total: 11.3ms	remaining: 22.6s
1:	learn: 69748.5922381	test: 70204.2414578	best: 70204.2414578 (1)	total: 21.9ms	remaining: 21.9s
2:	learn: 68333.9046047	test: 68749.9145215	best: 68749.9145215 (2)	total: 31.9ms	remaining: 21.3s
3:	learn: 66961.6835740	test: 67294.2895724	best: 67294.2895724 (3)	total: 39.9ms	remaining: 19.9s
4:	learn: 65621.3573762	test: 65863.7708437	best: 65863.7708437 (4)	total: 45ms	remaining: 18s
5:	learn: 64293.2963829	test: 64420.5928510	best: 64420.5928510 (5)	total: 53.8ms	remaining: 17.9s
6:	learn: 63052.3593471	test: 63136.1223079	best: 63136.1223079 (6)	total: 59.8ms	remaining: 17s
7:	learn: 61828.6054131	test: 61823.4737679	best: 61823.4737679 (7)	total: 66ms	remaining: 16.4s
8:	learn: 61389.1193602	test: 61316.4244346	best: 61316.4244346 (8)	total: 71.7ms	remaining: 15.9s
9:	learn: 60974.3047584	test: 60834.9764435	best: 60834.9764435 (9)	total: 74.1ms	remaining: 14.7s
10:	learn: 59577.1

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72414.1503114	test: 69317.4501365	best: 69317.4501365 (0)	total: 9.34ms	remaining: 18.7s
1:	learn: 70478.9897135	test: 67404.1131135	best: 67404.1131135 (1)	total: 19.3ms	remaining: 19.3s
2:	learn: 69032.8402702	test: 65935.5373058	best: 65935.5373058 (2)	total: 28.4ms	remaining: 18.9s
3:	learn: 67628.6224762	test: 64517.4982282	best: 64517.4982282 (3)	total: 36.1ms	remaining: 18s
4:	learn: 65482.7380672	test: 62417.3207722	best: 62417.3207722 (4)	total: 43ms	remaining: 17.1s
5:	learn: 63766.0843314	test: 60891.0754062	best: 60891.0754062 (5)	total: 50.2ms	remaining: 16.7s
6:	learn: 62453.8353434	test: 59640.9629196	best: 59640.9629196 (6)	total: 59.5ms	remaining: 16.9s
7:	learn: 61206.2629440	test: 58422.2120549	best: 58422.2120549 (7)	total: 69.5ms	remaining: 17.3s
8:	learn: 59713.9327827	test: 57007.6074978	best: 57007.6074978 (8)	total: 76.5ms	remaining: 16.9s
9:	learn: 58709.5067874	test: 55960.7164523	best: 55960.7164523 (9)	total: 81.4ms	remaining: 16.2s
10:	learn: 576

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71163.5103753	test: 74234.3599113	best: 74234.3599113 (0)	total: 7.79ms	remaining: 15.6s
1:	learn: 69266.1182141	test: 72288.9749759	best: 72288.9749759 (1)	total: 19.3ms	remaining: 19.3s
2:	learn: 67837.7155426	test: 70899.6303800	best: 70899.6303800 (2)	total: 29ms	remaining: 19.3s
3:	learn: 66401.3278780	test: 69496.9948353	best: 69496.9948353 (3)	total: 37.4ms	remaining: 18.7s
4:	learn: 64331.3263794	test: 67326.4982477	best: 67326.4982477 (4)	total: 58.4ms	remaining: 23.3s
5:	learn: 62722.9615003	test: 65732.4856493	best: 65732.4856493 (5)	total: 69.7ms	remaining: 23.2s
6:	learn: 61443.7228060	test: 64423.3184539	best: 64423.3184539 (6)	total: 82.2ms	remaining: 23.4s
7:	learn: 60209.4175047	test: 63143.3560470	best: 63143.3560470 (7)	total: 89.8ms	remaining: 22.4s
8:	learn: 58699.5422982	test: 61644.5928416	best: 61644.5928416 (8)	total: 99.2ms	remaining: 21.9s
9:	learn: 57555.1650733	test: 60505.7472431	best: 60505.7472431 (9)	total: 105ms	remaining: 20.9s
10:	learn: 56

「所要時間」も除いたら悪化した。「部屋数」を元に戻して、「所要時間」だけ除かれた状態にしてみる。

In [28]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [29]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71390.8269661	test: 70265.0981217	best: 70265.0981217 (0)	total: 8.12ms	remaining: 16.2s
1:	learn: 69340.2159283	test: 68453.4888020	best: 68453.4888020 (1)	total: 14.9ms	remaining: 14.9s
2:	learn: 67761.0997840	test: 66929.9546895	best: 66929.9546895 (2)	total: 22.1ms	remaining: 14.7s
3:	learn: 65856.4887238	test: 65268.8934591	best: 65268.8934591 (3)	total: 29.4ms	remaining: 14.7s
4:	learn: 64597.8986160	test: 64001.4022867	best: 64001.4022867 (4)	total: 38.8ms	remaining: 15.5s
5:	learn: 62970.5906808	test: 62493.3343357	best: 62493.3343357 (5)	total: 47.7ms	remaining: 15.8s
6:	learn: 61664.0242737	test: 61402.2700557	best: 61402.2700557 (6)	total: 54.5ms	remaining: 15.5s
7:	learn: 60542.0860379	test: 60310.4028155	best: 60310.4028155 (7)	total: 59ms	remaining: 14.7s
8:	learn: 58797.0624340	test: 58580.1132305	best: 58580.1132305 (8)	total: 69ms	remaining: 15.3s
9:	learn: 57937.4116204	test: 57716.7830505	best: 57716.7830505 (9)	total: 78.5ms	remaining: 15.6s
10:	learn: 570

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71090.9096028	test: 71510.2165905	best: 71510.2165905 (0)	total: 8.36ms	remaining: 16.7s
1:	learn: 69175.4945105	test: 69502.3161428	best: 69502.3161428 (1)	total: 16.1ms	remaining: 16.1s
2:	learn: 67645.3064793	test: 67927.7106120	best: 67927.7106120 (2)	total: 23.2ms	remaining: 15.5s
3:	learn: 65844.9300608	test: 66040.1037089	best: 66040.1037089 (3)	total: 30.5ms	remaining: 15.2s
4:	learn: 64552.7100284	test: 64682.5232662	best: 64682.5232662 (4)	total: 39.5ms	remaining: 15.8s
5:	learn: 62948.5304140	test: 63092.0035349	best: 63092.0035349 (5)	total: 45.8ms	remaining: 15.2s
6:	learn: 61749.3065911	test: 61716.6822870	best: 61716.6822870 (6)	total: 52.4ms	remaining: 14.9s
7:	learn: 60654.1250815	test: 60610.9860724	best: 60610.9860724 (7)	total: 57.7ms	remaining: 14.4s
8:	learn: 58927.6719060	test: 58835.4639065	best: 58835.4639065 (8)	total: 76.8ms	remaining: 17s
9:	learn: 58070.8712394	test: 57976.0222169	best: 57976.0222169 (9)	total: 92.8ms	remaining: 18.5s
10:	learn: 5

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71048.2874987	test: 71512.2180587	best: 71512.2180587 (0)	total: 10.3ms	remaining: 20.7s
1:	learn: 69122.9019948	test: 69458.1753089	best: 69458.1753089 (1)	total: 18.5ms	remaining: 18.5s
2:	learn: 67618.9791827	test: 67846.5050279	best: 67846.5050279 (2)	total: 26.6ms	remaining: 17.7s
3:	learn: 65807.2156447	test: 65843.1499238	best: 65843.1499238 (3)	total: 33.4ms	remaining: 16.7s
4:	learn: 64555.7510074	test: 64457.3787817	best: 64457.3787817 (4)	total: 41.5ms	remaining: 16.6s
5:	learn: 62968.1048327	test: 62796.2280580	best: 62796.2280580 (5)	total: 48.9ms	remaining: 16.3s
6:	learn: 61770.6235164	test: 61524.7231139	best: 61524.7231139 (6)	total: 56ms	remaining: 15.9s
7:	learn: 60690.0613508	test: 60355.1519361	best: 60355.1519361 (7)	total: 61.1ms	remaining: 15.2s
8:	learn: 58996.1017837	test: 58471.2754833	best: 58471.2754833 (8)	total: 71.3ms	remaining: 15.8s
9:	learn: 58229.6779716	test: 57599.5145207	best: 57599.5145207 (9)	total: 78ms	remaining: 15.5s
10:	learn: 575

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71748.1108779	test: 68851.2379570	best: 68851.2379570 (0)	total: 9.03ms	remaining: 18s
1:	learn: 69816.7666885	test: 66913.3625571	best: 66913.3625571 (1)	total: 17.3ms	remaining: 17.3s
2:	learn: 68271.9094112	test: 65364.2656200	best: 65364.2656200 (2)	total: 25.1ms	remaining: 16.7s
3:	learn: 66377.2938934	test: 63630.6888049	best: 63630.6888049 (3)	total: 31.9ms	remaining: 15.9s
4:	learn: 65112.3622513	test: 62421.7145824	best: 62421.7145824 (4)	total: 40ms	remaining: 16s
5:	learn: 63612.2498468	test: 60921.5925343	best: 60921.5925343 (5)	total: 48.4ms	remaining: 16.1s
6:	learn: 62174.9456226	test: 59526.5515645	best: 59526.5515645 (6)	total: 55.9ms	remaining: 15.9s
7:	learn: 60754.4675503	test: 58195.6542855	best: 58195.6542855 (7)	total: 62.6ms	remaining: 15.6s
8:	learn: 59560.7508772	test: 57017.6697025	best: 57017.6697025 (8)	total: 67.2ms	remaining: 14.9s
9:	learn: 58620.1577369	test: 56070.9346072	best: 56070.9346072 (9)	total: 70.9ms	remaining: 14.1s
10:	learn: 57091

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 70587.9389461	test: 73666.4901823	best: 73666.4901823 (0)	total: 10.5ms	remaining: 21s
1:	learn: 68749.2780965	test: 71751.8226276	best: 71751.8226276 (1)	total: 18.3ms	remaining: 18.3s
2:	learn: 67242.7452767	test: 70192.1097093	best: 70192.1097093 (2)	total: 25.8ms	remaining: 17.2s
3:	learn: 65465.1808880	test: 68266.6370775	best: 68266.6370775 (3)	total: 31.5ms	remaining: 15.7s
4:	learn: 64228.9227554	test: 66984.7866423	best: 66984.7866423 (4)	total: 39.9ms	remaining: 15.9s
5:	learn: 62668.2769790	test: 65316.5257865	best: 65316.5257865 (5)	total: 46.7ms	remaining: 15.5s
6:	learn: 61238.5326522	test: 63893.6953480	best: 63893.6953480 (6)	total: 53.8ms	remaining: 15.3s
7:	learn: 59998.7720167	test: 62676.2354379	best: 62676.2354379 (7)	total: 60.5ms	remaining: 15.1s
8:	learn: 58706.0268001	test: 61320.9185372	best: 61320.9185372 (8)	total: 66.3ms	remaining: 14.7s
9:	learn: 57334.2402737	test: 59910.2207940	best: 59910.2207940 (9)	total: 73ms	remaining: 14.5s
10:	learn: 562

やはり「部屋数」だけを除いた時の方が良い

### カテゴリ変数で除いた方が良いものはないか検証する 

まずは「K」を除外してみる

In [32]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [33]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72560.6614744	test: 71285.5900781	best: 71285.5900781 (0)	total: 7.83ms	remaining: 15.7s
1:	learn: 70688.4970705	test: 69530.5397892	best: 69530.5397892 (1)	total: 17.3ms	remaining: 17.3s
2:	learn: 68836.9077414	test: 67840.2440384	best: 67840.2440384 (2)	total: 22ms	remaining: 14.7s
3:	learn: 67371.6547764	test: 66408.3016684	best: 66408.3016684 (3)	total: 26.2ms	remaining: 13.1s
4:	learn: 65855.0433259	test: 64997.0950843	best: 64997.0950843 (4)	total: 33ms	remaining: 13.2s
5:	learn: 64368.7221929	test: 63738.0390823	best: 63738.0390823 (5)	total: 41.7ms	remaining: 13.9s
6:	learn: 63289.2061171	test: 62848.1426390	best: 62848.1426390 (6)	total: 44.6ms	remaining: 12.7s
7:	learn: 61622.8034339	test: 61330.3378843	best: 61330.3378843 (7)	total: 52.7ms	remaining: 13.1s
8:	learn: 60211.9976255	test: 60027.5091017	best: 60027.5091017 (8)	total: 60.7ms	remaining: 13.4s
9:	learn: 58987.9881615	test: 58812.6699782	best: 58812.6699782 (9)	total: 67.7ms	remaining: 13.5s
10:	learn: 576

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72220.3659745	test: 72753.4237805	best: 72753.4237805 (0)	total: 8.98ms	remaining: 17.9s
1:	learn: 70336.9456964	test: 70863.6679882	best: 70863.6679882 (1)	total: 18.4ms	remaining: 18.4s
2:	learn: 68471.1617682	test: 68890.8100614	best: 68890.8100614 (2)	total: 22.6ms	remaining: 15.1s
3:	learn: 66786.3837018	test: 67155.7661939	best: 67155.7661939 (3)	total: 28.9ms	remaining: 14.4s
4:	learn: 65071.8385125	test: 65442.2600219	best: 65442.2600219 (4)	total: 38.2ms	remaining: 15.3s
5:	learn: 63766.6002269	test: 64150.3866212	best: 64150.3866212 (5)	total: 46.8ms	remaining: 15.5s
6:	learn: 62255.8684089	test: 62581.4584694	best: 62581.4584694 (6)	total: 54.1ms	remaining: 15.4s
7:	learn: 60857.6888879	test: 61177.5854506	best: 61177.5854506 (7)	total: 59.8ms	remaining: 14.9s
8:	learn: 59699.7571784	test: 59960.3682105	best: 59960.3682105 (8)	total: 66.3ms	remaining: 14.7s
9:	learn: 58648.8560922	test: 58876.8147415	best: 58876.8147415 (9)	total: 75.7ms	remaining: 15.1s
10:	learn:

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72170.9860306	test: 72834.7294962	best: 72834.7294962 (0)	total: 10ms	remaining: 20s
1:	learn: 70288.6478829	test: 70801.7371277	best: 70801.7371277 (1)	total: 34.2ms	remaining: 34.1s
2:	learn: 68440.9622649	test: 68729.2994373	best: 68729.2994373 (2)	total: 43.5ms	remaining: 28.9s
3:	learn: 66777.9042317	test: 66871.3158800	best: 66871.3158800 (3)	total: 51.7ms	remaining: 25.8s
4:	learn: 65091.3737131	test: 65093.0960994	best: 65093.0960994 (4)	total: 65.3ms	remaining: 26s
5:	learn: 63797.0133092	test: 63690.0672675	best: 63690.0672675 (5)	total: 73.4ms	remaining: 24.4s
6:	learn: 62324.3201726	test: 62111.3927714	best: 62111.3927714 (6)	total: 79.9ms	remaining: 22.8s
7:	learn: 61048.2448977	test: 60769.1631434	best: 60769.1631434 (7)	total: 86.7ms	remaining: 21.6s
8:	learn: 59501.2508776	test: 59079.6226413	best: 59079.6226413 (8)	total: 93.3ms	remaining: 20.6s
9:	learn: 58470.1651001	test: 57952.9552353	best: 57952.9552353 (9)	total: 96.8ms	remaining: 19.3s
10:	learn: 57215

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72937.9611653	test: 69838.0089089	best: 69838.0089089 (0)	total: 9.22ms	remaining: 18.4s
1:	learn: 71053.0903699	test: 67990.1298076	best: 67990.1298076 (1)	total: 19.8ms	remaining: 19.7s
2:	learn: 69228.6268762	test: 66324.0853529	best: 66324.0853529 (2)	total: 30.2ms	remaining: 20.1s
3:	learn: 67415.7997480	test: 64552.2154363	best: 64552.2154363 (3)	total: 38.3ms	remaining: 19.1s
4:	learn: 65666.1170684	test: 62834.4042320	best: 62834.4042320 (4)	total: 47.7ms	remaining: 19s
5:	learn: 64220.1300312	test: 61349.1401127	best: 61349.1401127 (5)	total: 54.2ms	remaining: 18s
6:	learn: 62865.8079851	test: 60018.1623615	best: 60018.1623615 (6)	total: 62.7ms	remaining: 17.8s
7:	learn: 61554.5891143	test: 58681.9965545	best: 58681.9965545 (7)	total: 70.6ms	remaining: 17.6s
8:	learn: 60439.4570424	test: 57619.2769383	best: 57619.2769383 (8)	total: 73.4ms	remaining: 16.2s
9:	learn: 59420.3381516	test: 56599.3470877	best: 56599.3470877 (9)	total: 79ms	remaining: 15.7s
10:	learn: 58573

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71689.2758928	test: 74874.1340056	best: 74874.1340056 (0)	total: 7.38ms	remaining: 14.7s
1:	learn: 69808.4533427	test: 72838.1453790	best: 72838.1453790 (1)	total: 19ms	remaining: 18.9s
2:	learn: 68348.5782641	test: 71404.8224094	best: 71404.8224094 (2)	total: 22.8ms	remaining: 15.2s
3:	learn: 66604.5454797	test: 69640.8578992	best: 69640.8578992 (3)	total: 29.7ms	remaining: 14.8s
4:	learn: 65415.5526962	test: 68386.7943448	best: 68386.7943448 (4)	total: 38.3ms	remaining: 15.3s
5:	learn: 64096.1235989	test: 67066.8778166	best: 67066.8778166 (5)	total: 46ms	remaining: 15.3s
6:	learn: 62552.3617871	test: 65478.4056205	best: 65478.4056205 (6)	total: 53.7ms	remaining: 15.3s
7:	learn: 61407.3276559	test: 64385.6361528	best: 64385.6361528 (7)	total: 58ms	remaining: 14.4s
8:	learn: 60386.4018564	test: 63336.3722072	best: 63336.3722072 (8)	total: 66.1ms	remaining: 14.6s
9:	learn: 59199.9116857	test: 62127.9704233	best: 62127.9704233 (9)	total: 73.6ms	remaining: 14.7s
10:	learn: 57353

多少の改善

「S」も除外してみる

In [34]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D"]],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [35]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72177.9472353	test: 70849.8297127	best: 70849.8297127 (0)	total: 6.18ms	remaining: 12.4s
1:	learn: 71470.8076211	test: 70167.1430031	best: 70167.1430031 (1)	total: 13.1ms	remaining: 13.1s
2:	learn: 69723.0048586	test: 68455.6064618	best: 68455.6064618 (2)	total: 22.1ms	remaining: 14.7s
3:	learn: 68614.5338686	test: 67448.7156810	best: 67448.7156810 (3)	total: 25.4ms	remaining: 12.7s
4:	learn: 66760.1349711	test: 65736.8175292	best: 65736.8175292 (4)	total: 34.6ms	remaining: 13.8s
5:	learn: 65103.7746272	test: 64131.2809276	best: 64131.2809276 (5)	total: 43.3ms	remaining: 14.4s
6:	learn: 63822.3797026	test: 62904.4935484	best: 62904.4935484 (6)	total: 47.1ms	remaining: 13.4s
7:	learn: 62135.5742447	test: 61405.8440409	best: 61405.8440409 (7)	total: 53.5ms	remaining: 13.3s
8:	learn: 60798.5253493	test: 60150.8468550	best: 60150.8468550 (8)	total: 61.7ms	remaining: 13.6s
9:	learn: 59619.9888091	test: 59216.3789129	best: 59216.3789129 (9)	total: 68.5ms	remaining: 13.6s
10:	learn:

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71824.3951544	test: 72336.1266206	best: 72336.1266206 (0)	total: 5.79ms	remaining: 11.6s
1:	learn: 71226.5601906	test: 71697.2472552	best: 71697.2472552 (1)	total: 9.64ms	remaining: 9.63s
2:	learn: 69474.8393996	test: 69960.2534427	best: 69960.2534427 (2)	total: 19.5ms	remaining: 13s
3:	learn: 67721.6103495	test: 67950.7253177	best: 67950.7253177 (3)	total: 28.2ms	remaining: 14.1s
4:	learn: 65920.3156533	test: 66160.7147943	best: 66160.7147943 (4)	total: 36.1ms	remaining: 14.4s
5:	learn: 64526.8150751	test: 64723.9039286	best: 64723.9039286 (5)	total: 39.7ms	remaining: 13.2s
6:	learn: 63297.6667611	test: 63468.3653169	best: 63468.3653169 (6)	total: 45.9ms	remaining: 13.1s
7:	learn: 62111.5784339	test: 62305.4428388	best: 62305.4428388 (7)	total: 54.7ms	remaining: 13.6s
8:	learn: 61094.8037778	test: 61213.7276538	best: 61213.7276538 (8)	total: 63.8ms	remaining: 14.1s
9:	learn: 60057.4592399	test: 60141.1536404	best: 60141.1536404 (9)	total: 68ms	remaining: 13.5s
10:	learn: 586

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71849.6831040	test: 72378.0066208	best: 72378.0066208 (0)	total: 6.35ms	remaining: 12.7s
1:	learn: 71189.2721216	test: 71649.1154129	best: 71649.1154129 (1)	total: 13.8ms	remaining: 13.8s
2:	learn: 69486.0712340	test: 69784.3179347	best: 69784.3179347 (2)	total: 23.1ms	remaining: 15.4s
3:	learn: 68413.3717705	test: 68656.0519204	best: 68656.0519204 (3)	total: 26.2ms	remaining: 13.1s
4:	learn: 66822.6184789	test: 66821.0452982	best: 66821.0452982 (4)	total: 33.5ms	remaining: 13.3s
5:	learn: 65121.8836295	test: 64917.2730811	best: 64917.2730811 (5)	total: 41.1ms	remaining: 13.6s
6:	learn: 63311.2891096	test: 63028.0074308	best: 63028.0074308 (6)	total: 49.2ms	remaining: 14s
7:	learn: 61638.8287127	test: 61201.5075928	best: 61201.5075928 (7)	total: 55.9ms	remaining: 13.9s
8:	learn: 60376.9020700	test: 59782.6524541	best: 59782.6524541 (8)	total: 64.8ms	remaining: 14.3s
9:	learn: 59229.1552369	test: 58558.4785916	best: 58558.4785916 (9)	total: 70.5ms	remaining: 14s
10:	learn: 583

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72548.1380771	test: 69490.4408785	best: 69490.4408785 (0)	total: 5.98ms	remaining: 11.9s
1:	learn: 71912.9267884	test: 68767.2130468	best: 68767.2130468 (1)	total: 12ms	remaining: 12s
2:	learn: 70166.4432307	test: 67150.4480369	best: 67150.4480369 (2)	total: 21.9ms	remaining: 14.6s
3:	learn: 69062.6466063	test: 66071.7940172	best: 66071.7940172 (3)	total: 26ms	remaining: 13s
4:	learn: 67272.2683746	test: 64312.1131468	best: 64312.1131468 (4)	total: 34.7ms	remaining: 13.9s
5:	learn: 65608.0501592	test: 62798.5912957	best: 62798.5912957 (5)	total: 42.2ms	remaining: 14s
6:	learn: 64340.4775591	test: 61531.2871396	best: 61531.2871396 (6)	total: 45.3ms	remaining: 12.9s
7:	learn: 62705.0464176	test: 59913.9968179	best: 59913.9968179 (7)	total: 52.9ms	remaining: 13.2s
8:	learn: 61376.1951103	test: 58609.8012333	best: 58609.8012333 (8)	total: 61.7ms	remaining: 13.6s
9:	learn: 59731.7535149	test: 57031.1744261	best: 57031.1744261 (9)	total: 69ms	remaining: 13.7s
10:	learn: 58603.64916

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71303.9688706	test: 74419.5111902	best: 74419.5111902 (0)	total: 5.6ms	remaining: 11.2s
1:	learn: 70647.2641265	test: 73665.7298495	best: 73665.7298495 (1)	total: 12.9ms	remaining: 12.8s
2:	learn: 68957.3758822	test: 71865.4697678	best: 71865.4697678 (2)	total: 22.8ms	remaining: 15.2s
3:	learn: 67935.1132956	test: 70755.3924260	best: 70755.3924260 (3)	total: 26.8ms	remaining: 13.4s
4:	learn: 66362.6069390	test: 69029.9812353	best: 69029.9812353 (4)	total: 43ms	remaining: 17.2s
5:	learn: 64790.1110271	test: 67517.7738462	best: 67517.7738462 (5)	total: 59.2ms	remaining: 19.7s
6:	learn: 63707.2782388	test: 66374.4818574	best: 66374.4818574 (6)	total: 66.2ms	remaining: 18.9s
7:	learn: 62406.3004844	test: 65066.0209534	best: 65066.0209534 (7)	total: 73ms	remaining: 18.2s
8:	learn: 61261.1307047	test: 63999.6913488	best: 63999.6913488 (8)	total: 78.8ms	remaining: 17.4s
9:	learn: 59576.3871185	test: 62143.7656835	best: 62143.7656835 (9)	total: 90ms	remaining: 17.9s
10:	learn: 58249.

悪化している。

それでは「部屋数」とカテゴリ変数の「K」の二つが除かれている状況はどうか

In [36]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["L","D","S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["L","D",'S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [37]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71960.4426955	test: 70689.3978924	best: 70689.3978924 (0)	total: 8.76ms	remaining: 17.5s
1:	learn: 70373.1631624	test: 69209.8311251	best: 69209.8311251 (1)	total: 16.8ms	remaining: 16.8s
2:	learn: 68441.7573384	test: 67472.6393688	best: 67472.6393688 (2)	total: 24.7ms	remaining: 16.4s
3:	learn: 67104.1764504	test: 66136.3656820	best: 66136.3656820 (3)	total: 27.9ms	remaining: 13.9s
4:	learn: 65578.9904312	test: 64630.2802966	best: 64630.2802966 (4)	total: 34.4ms	remaining: 13.7s
5:	learn: 63695.7926100	test: 62995.7085330	best: 62995.7085330 (5)	total: 42.2ms	remaining: 14s
6:	learn: 61953.3058712	test: 61350.7060549	best: 61350.7060549 (6)	total: 50.4ms	remaining: 14.3s
7:	learn: 60698.0918110	test: 60167.2776190	best: 60167.2776190 (7)	total: 59.3ms	remaining: 14.8s
8:	learn: 60330.1622449	test: 59809.0262599	best: 59809.0262599 (8)	total: 62.1ms	remaining: 13.7s
9:	learn: 58926.1000782	test: 58685.4357120	best: 58685.4357120 (9)	total: 70.4ms	remaining: 14s
10:	learn: 577

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71619.0222559	test: 72158.8291376	best: 72158.8291376 (0)	total: 10.1ms	remaining: 20.1s
1:	learn: 70051.4375688	test: 70606.8177057	best: 70606.8177057 (1)	total: 17.8ms	remaining: 17.8s
2:	learn: 68182.4202910	test: 68705.0957678	best: 68705.0957678 (2)	total: 25.7ms	remaining: 17.1s
3:	learn: 66890.9452452	test: 67367.9691513	best: 67367.9691513 (3)	total: 29.6ms	remaining: 14.8s
4:	learn: 64992.1436777	test: 65360.9530918	best: 65360.9530918 (4)	total: 37.8ms	remaining: 15.1s
5:	learn: 63420.2270223	test: 63798.0559180	best: 63798.0559180 (5)	total: 46ms	remaining: 15.3s
6:	learn: 62554.3495233	test: 62934.9680943	best: 62934.9680943 (6)	total: 48.6ms	remaining: 13.8s
7:	learn: 60571.7329854	test: 60977.9792451	best: 60977.9792451 (7)	total: 56.8ms	remaining: 14.1s
8:	learn: 59349.0043264	test: 59770.1094031	best: 59770.1094031 (8)	total: 63.5ms	remaining: 14.1s
9:	learn: 58148.0176329	test: 58554.0314976	best: 58554.0314976 (9)	total: 73.6ms	remaining: 14.6s
10:	learn: 5

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71611.5834307	test: 72183.8274547	best: 72183.8274547 (0)	total: 7.94ms	remaining: 15.9s
1:	learn: 70064.4329711	test: 70577.0723477	best: 70577.0723477 (1)	total: 19.3ms	remaining: 19.3s
2:	learn: 68194.0427814	test: 68663.1767542	best: 68663.1767542 (2)	total: 28ms	remaining: 18.7s
3:	learn: 66902.5410787	test: 67236.4904375	best: 67236.4904375 (3)	total: 35.7ms	remaining: 17.8s
4:	learn: 65443.8321308	test: 65686.2520659	best: 65686.2520659 (4)	total: 42.3ms	remaining: 16.9s
5:	learn: 63871.0799907	test: 64035.8463621	best: 64035.8463621 (5)	total: 48.9ms	remaining: 16.3s
6:	learn: 62127.8905573	test: 62116.0377947	best: 62116.0377947 (6)	total: 56.3ms	remaining: 16s
7:	learn: 60606.0660835	test: 60448.9106614	best: 60448.9106614 (7)	total: 64.9ms	remaining: 16.2s
8:	learn: 59421.1074388	test: 59193.3216311	best: 59193.3216311 (8)	total: 74.2ms	remaining: 16.4s
9:	learn: 58323.6027196	test: 58014.8594482	best: 58014.8594482 (9)	total: 81.1ms	remaining: 16.1s
10:	learn: 571

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72294.6038129	test: 69284.5883167	best: 69284.5883167 (0)	total: 7.71ms	remaining: 15.4s
1:	learn: 70721.6829460	test: 67692.9758556	best: 67692.9758556 (1)	total: 17.8ms	remaining: 17.8s
2:	learn: 68891.2216814	test: 65867.4781060	best: 65867.4781060 (2)	total: 26.5ms	remaining: 17.6s
3:	learn: 67579.0285175	test: 64509.0612362	best: 64509.0612362 (3)	total: 35.7ms	remaining: 17.8s
4:	learn: 66065.5129970	test: 63109.6672775	best: 63109.6672775 (4)	total: 41.8ms	remaining: 16.7s
5:	learn: 64444.0227862	test: 61586.4461093	best: 61586.4461093 (5)	total: 48.8ms	remaining: 16.2s
6:	learn: 62752.9134875	test: 59804.5655899	best: 59804.5655899 (6)	total: 55.8ms	remaining: 15.9s
7:	learn: 61173.6469657	test: 58304.3262502	best: 58304.3262502 (7)	total: 64ms	remaining: 15.9s
8:	learn: 59948.5662266	test: 57077.7036833	best: 57077.7036833 (8)	total: 73.3ms	remaining: 16.2s
9:	learn: 58835.1593927	test: 56006.1490647	best: 56006.1490647 (9)	total: 80.8ms	remaining: 16.1s
10:	learn: 5

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71087.2289000	test: 74207.4605208	best: 74207.4605208 (0)	total: 8.81ms	remaining: 17.6s
1:	learn: 69529.7862587	test: 72650.4084184	best: 72650.4084184 (1)	total: 17.7ms	remaining: 17.7s
2:	learn: 67743.3397027	test: 70820.5288448	best: 70820.5288448 (2)	total: 26.4ms	remaining: 17.6s
3:	learn: 66437.2633613	test: 69506.1776403	best: 69506.1776403 (3)	total: 34.2ms	remaining: 17s
4:	learn: 64948.2798948	test: 67966.0357497	best: 67966.0357497 (4)	total: 39.8ms	remaining: 15.9s
5:	learn: 63288.5951973	test: 66491.0675078	best: 66491.0675078 (5)	total: 46.2ms	remaining: 15.4s
6:	learn: 61632.6585161	test: 64748.9314456	best: 64748.9314456 (6)	total: 53.9ms	remaining: 15.3s
7:	learn: 60091.4567514	test: 63136.3415009	best: 63136.3415009 (7)	total: 61.5ms	remaining: 15.3s
8:	learn: 58893.4825878	test: 61881.1975225	best: 61881.1975225 (8)	total: 70.7ms	remaining: 15.6s
9:	learn: 57779.7723777	test: 60752.2024899	best: 60752.2024899 (9)	total: 77.8ms	remaining: 15.5s
10:	learn: 5

## CatBoostにおいては、「温水洗浄便座」と「方角」と「キッチン」を除いたもので出力することにする！

In [52]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [53]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    model = CatBoostRegressor(
        loss_function='RMSE', 
        iterations = 2000, 
        learning_rate=0.05, 
        depth=7, 
        l2_leaf_reg= 1.7538232373118053e-06, 
        random_strength=26, 
        bagging_temperature = 12.500712230836259,
        od_type='Iter',
        # od_wait = 10
        )

    train_pool = Pool(X_tr, label=y_tr, cat_features=category_lists)
    valid_pool = Pool(X_val, label=y_val, cat_features=category_lists)

    model.fit(train_pool, eval_set=valid_pool, use_best_model=True, early_stopping_rounds=10, plot=True)

y_pred = model.predict(X_test)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72725.6816902	test: 71381.2629992	best: 71381.2629992 (0)	total: 2.33ms	remaining: 4.65s
1:	learn: 70876.6266270	test: 69554.7063760	best: 69554.7063760 (1)	total: 11.6ms	remaining: 11.6s
2:	learn: 69764.6658991	test: 68549.5742581	best: 68549.5742581 (2)	total: 19.9ms	remaining: 13.2s
3:	learn: 68724.8024460	test: 67530.6036925	best: 67530.6036925 (3)	total: 22.5ms	remaining: 11.2s
4:	learn: 67118.5699521	test: 65976.5425801	best: 65976.5425801 (4)	total: 28.5ms	remaining: 11.4s
5:	learn: 65515.8643388	test: 64613.7713007	best: 64613.7713007 (5)	total: 37.5ms	remaining: 12.5s
6:	learn: 63485.4577542	test: 62789.3779271	best: 62789.3779271 (6)	total: 46.5ms	remaining: 13.3s
7:	learn: 62094.4295248	test: 61455.4334710	best: 61455.4334710 (7)	total: 53.4ms	remaining: 13.3s
8:	learn: 60477.3875415	test: 60054.8541645	best: 60054.8541645 (8)	total: 63.6ms	remaining: 14.1s
9:	learn: 59316.3754626	test: 59033.4093812	best: 59033.4093812 (9)	total: 72.1ms	remaining: 14.3s
10:	learn:

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72360.5459165	test: 72880.1979329	best: 72880.1979329 (0)	total: 2.34ms	remaining: 4.68s
1:	learn: 70484.2374647	test: 70969.3146988	best: 70969.3146988 (1)	total: 11.7ms	remaining: 11.7s
2:	learn: 68752.4248891	test: 69237.0995712	best: 69237.0995712 (2)	total: 20.9ms	remaining: 13.9s
3:	learn: 67207.0000796	test: 67586.3391243	best: 67586.3391243 (3)	total: 28ms	remaining: 14s
4:	learn: 65701.7418006	test: 66009.1380175	best: 66009.1380175 (4)	total: 36.7ms	remaining: 14.6s
5:	learn: 64143.7007506	test: 64411.0659361	best: 64411.0659361 (5)	total: 43.1ms	remaining: 14.3s
6:	learn: 62752.6940862	test: 62918.5261806	best: 62918.5261806 (6)	total: 49.1ms	remaining: 14s
7:	learn: 61024.4180596	test: 61113.0470014	best: 61113.0470014 (7)	total: 57.6ms	remaining: 14.4s
8:	learn: 59806.9678603	test: 59820.9115101	best: 59820.9115101 (8)	total: 67.6ms	remaining: 15s
9:	learn: 58025.5220169	test: 58055.1190783	best: 58055.1190783 (9)	total: 74.6ms	remaining: 14.9s
10:	learn: 57211.2

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 72352.6352553	test: 72946.5643571	best: 72946.5643571 (0)	total: 2.51ms	remaining: 5.01s
1:	learn: 70090.7327693	test: 70528.9747704	best: 70528.9747704 (1)	total: 12.9ms	remaining: 12.8s
2:	learn: 69262.0843452	test: 69483.6788708	best: 69483.6788708 (2)	total: 21.8ms	remaining: 14.5s
3:	learn: 67673.9310345	test: 67756.4217057	best: 67756.4217057 (3)	total: 30.7ms	remaining: 15.3s
4:	learn: 66148.6787707	test: 66166.8103971	best: 66166.8103971 (4)	total: 39.3ms	remaining: 15.7s
5:	learn: 64394.6857133	test: 64309.1284555	best: 64309.1284555 (5)	total: 47.1ms	remaining: 15.7s
6:	learn: 62860.6343062	test: 62669.1463244	best: 62669.1463244 (6)	total: 53.6ms	remaining: 15.2s
7:	learn: 61280.8548752	test: 60911.8089293	best: 60911.8089293 (7)	total: 57.7ms	remaining: 14.4s
8:	learn: 59689.3525736	test: 59105.3090859	best: 59105.3090859 (8)	total: 64.2ms	remaining: 14.2s
9:	learn: 58613.5716749	test: 57940.2543089	best: 57940.2543089 (9)	total: 70.6ms	remaining: 14.1s
10:	learn:

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 73051.7306245	test: 70023.0638894	best: 70023.0638894 (0)	total: 2.69ms	remaining: 5.37s
1:	learn: 71209.0929141	test: 68284.8261815	best: 68284.8261815 (1)	total: 13.7ms	remaining: 13.7s
2:	learn: 70137.4328323	test: 67183.0652265	best: 67183.0652265 (2)	total: 21.4ms	remaining: 14.2s
3:	learn: 68540.9548466	test: 65579.4233257	best: 65579.4233257 (3)	total: 30.1ms	remaining: 15s
4:	learn: 67025.4625972	test: 64088.7995873	best: 64088.7995873 (4)	total: 37.6ms	remaining: 15s
5:	learn: 65243.2618411	test: 62356.5952273	best: 62356.5952273 (5)	total: 44ms	remaining: 14.6s
6:	learn: 64042.4948441	test: 61145.1085308	best: 61145.1085308 (6)	total: 47.2ms	remaining: 13.4s
7:	learn: 63392.8060542	test: 60434.7062913	best: 60434.7062913 (7)	total: 53.9ms	remaining: 13.4s
8:	learn: 61769.1507303	test: 58830.4750358	best: 58830.4750358 (8)	total: 63.4ms	remaining: 14s
9:	learn: 60254.8371886	test: 57380.8120367	best: 57380.8120367 (9)	total: 70.8ms	remaining: 14.1s
10:	learn: 58724.8

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 71818.5392550	test: 75007.9087839	best: 75007.9087839 (0)	total: 2.74ms	remaining: 5.48s
1:	learn: 70009.1854705	test: 73197.8265454	best: 73197.8265454 (1)	total: 14.2ms	remaining: 14.2s
2:	learn: 68952.4750475	test: 72073.9459919	best: 72073.9459919 (2)	total: 21ms	remaining: 14s
3:	learn: 67367.7263257	test: 70430.9441979	best: 70430.9441979 (3)	total: 30.2ms	remaining: 15.1s
4:	learn: 65895.4613945	test: 68941.1722462	best: 68941.1722462 (4)	total: 38.1ms	remaining: 15.2s
5:	learn: 64107.0506063	test: 67160.9520462	best: 67160.9520462 (5)	total: 44.6ms	remaining: 14.8s
6:	learn: 62569.1590904	test: 65642.1304493	best: 65642.1304493 (6)	total: 51.5ms	remaining: 14.7s
7:	learn: 60937.8985053	test: 63982.2392414	best: 63982.2392414 (7)	total: 59.7ms	remaining: 14.9s
8:	learn: 59629.7421614	test: 62627.2669368	best: 62627.2669368 (8)	total: 67.7ms	remaining: 15s
9:	learn: 58448.3472353	test: 61319.6395900	best: 61319.6395900 (9)	total: 75.7ms	remaining: 15.1s
10:	learn: 57369

In [54]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/CatBoost_cv_result.csv',index=False)